### e-Stat 【政府統計の総合窓口】データの利活用
https://www.e-stat.go.jp/ のデータを用いたheatmapによる可視化  
ネット上の情報取得から、データ処理・解析、可視化までをnotebbok上でワンストップで行う

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import japanize_matplotlib

%matplotlib inline
%config InlineBackend.figure_format = 'retina'

### 以下、ファイル読み込みと整形

In [2]:
# ガソリン販売量の都道府県別時系列データ
df0 = pd.read_csv('TimeSeriesResult_20220526074338419.csv')

# グラフ作成用のタイトルと規格化の際の基準年を取得
graphtitle = df0.columns[3]
ini_year = df0['時点'][0]
df0.tail()

時点  地域コード   地域  ガソリン販売量【kL】  注記
1675  2015年度  47000  沖縄県       593628 NaN
1676  2016年度  47000  沖縄県       700569 NaN
1677  2017年度  47000  沖縄県       691725 NaN
1678  2018年度  47000  沖縄県       699740 NaN
1679  2019年度  47000  沖縄県       691509 NaN

In [3]:
# 注記列を削除
df0.drop(['注記'], axis=1, inplace=True)
df0.head()

時点  地域コード  地域  ガソリン販売量【kL】
0  1985年度      0  全国     38830050
1  1986年度      0  全国     39637821
2  1987年度      0  全国     40761056
3  1988年度      0  全国     42631380
4  1989年度      0  全国     43289512

In [4]:
df0.rename(columns={df0.columns[-1]:'data'}, inplace=True)
df0.head()

時点  地域コード  地域      data
0  1985年度      0  全国  38830050
1  1986年度      0  全国  39637821
2  1987年度      0  全国  40761056
3  1988年度      0  全国  42631380
4  1989年度      0  全国  43289512

In [5]:
# 都道府県リストの取得
prefs = df0['地域'].unique().tolist()[1:]
print(prefs)

['北海道', '青森県', '岩手県', '宮城県', '秋田県', '山形県', '福島県', '茨城県', '栃木県', '群馬県', '埼玉県', '千葉県', '東京都', '神奈川県', '新潟県', '富山県', '石川県', '福井県', '山梨県', '長野県', '岐阜県', '静岡県', '愛知県', '三重県', '滋賀県', '京都府', '大阪府', '兵庫県', '奈良県', '和歌山県', '鳥取県', '島根県', '岡山県', '広島県', '山口県', '徳島県', '香川県', '愛媛県', '高知県', '福岡県', '佐賀県', '長崎県', '熊本県', '大分県', '宮崎県', '鹿児島県', '沖縄県']


In [6]:
a = df0.groupby('地域')
#a.get_group('北海道')
pref = prefs[0]
df = a.get_group(pref).rename(columns={'data': pref}).drop(['地域コード', '地域'], axis=1)
df.head()

時点      北海道
35  1985年度  1693383
36  1986年度  1669138
37  1987年度  1659235
38  1988年度  1694518
39  1989年度  1678936

In [7]:
for pref in prefs[1:]:
    df_tmp = a.get_group(pref).rename(columns={'data': pref}).drop(['地域コード', '地域'], axis=1)
    df = pd.merge(df, df_tmp, on='時点', how='left')
df.head()

時点      北海道     青森県     岩手県     宮城県     秋田県     山形県     福島県      茨城県  \
0  1985年度  1693383  434891  434575  782702  380122  380921  715219  1054713   
1  1986年度  1669138  431426  422072  809936  382926  371785  712438  1088797   
2  1987年度  1659235  433148  413245  841658  384960  379744  730761  1135242   
3  1988年度  1694518  440975  422419  884598  392333  389182  764984  1202633   
4  1989年度  1678936  441769  427618  880260  399686  393028  771637  1227117   

      栃木県  ...     愛媛県     高知県      福岡県     佐賀県     長崎県     熊本県     大分県  \
0  757472  ...  430556  270584  1601523  299694  404515  582845  379698   
1  784129  ...  437271  278936  1659655  316865  407824  589272  379934   
2  813348  ...  459069  284077  1655597  328561  410784  601072  395998   
3  858000  ...  472233  296640  1766326  344782  427630  622669  410069   
4  871196  ...  475147  299591  1700010  344533  443632  627062  417853   

      宮崎県    鹿児島県     沖縄県  
0  384990  559341  341592  
1  389229  574230  356124  
2  399095  589528  377631  
3  411383  621142  396566  
4  427102  618488  413114  

[5 rows x 48 columns]

In [8]:
# 列名を時点から年に変更
df.rename(columns={'時点': '年'},inplace=True)

# 年度を削除（ex. 2000年度 → 2000）
df['年'] = df['年'].apply(lambda x: x.replace('年度', ''))
df.set_index('年', inplace=True)
df.head()

北海道     青森県     岩手県     宮城県     秋田県     山形県     福島県      茨城県  \
年                                                                        
1985  1693383  434891  434575  782702  380122  380921  715219  1054713   
1986  1669138  431426  422072  809936  382926  371785  712438  1088797   
1987  1659235  433148  413245  841658  384960  379744  730761  1135242   
1988  1694518  440975  422419  884598  392333  389182  764984  1202633   
1989  1678936  441769  427618  880260  399686  393028  771637  1227117   

         栃木県     群馬県  ...     愛媛県     高知県      福岡県     佐賀県     長崎県     熊本県  \
年                     ...                                                    
1985  757472  782923  ...  430556  270584  1601523  299694  404515  582845   
1986  784129  798005  ...  437271  278936  1659655  316865  407824  589272   
1987  813348  818464  ...  459069  284077  1655597  328561  410784  601072   
1988  858000  850408  ...  472233  296640  1766326  344782  427630  622669   
1989  871196  871392  ...  475147  299591  1700010  344533  443632  627062   

         大分県     宮崎県    鹿児島県     沖縄県  
年                                     
1985  379698  384990  559341  341592  
1986  379934  389229  574230  356124  
1987  395998  399095  589528  377631  
1988  410069  411383  621142  396566  
1989  417853  427102  618488  413114  

[5 rows x 47 columns]

### 作成した dataframe のExcelへの保存
解析結果をExcelで出力してやり取りする場合などに利用

In [9]:
# 整形データのExcel形式での保存
df.to_excel(r"D:\users\desktop\gasoline_pref.xlsx")